In [1]:
%load_ext autoreload
%autoreload 2

# BTM用に､10000分割したテキストをre-clusteringするための分配処理

In [2]:
#loaderの設定などの練習
import json
from loaders.CommonCrawlDataset import CommonCrawlDataset

In [3]:
#10000分割されたjsonlファイルのパスを取得

import glob
import random

jsonl_path_list=glob.glob("../data/dedup_categorized/*/*.jsonl")
random.shuffle(jsonl_path_list)
cid_to_path_list={}
for jsonl_path in jsonl_path_list:
    cid=jsonl_path.split("/")[-2]
    if cid not in cid_to_path_list:
        cid_to_path_list[cid]=[]
    cid_to_path_list[cid].append(jsonl_path)

In [4]:
from tqdm import tqdm
#代表的な*件を取得
max_texts=10
cid_to_texts={}
for cid, path_list in tqdm(cid_to_path_list.items()):
    texts=[]
    for path in path_list:
        cnt=0
        with open(path) as f:
            for i, line in enumerate(f):
                t=json.loads(line)["text"]
                if len(t)<10:
                    continue
                texts.append(t)
                cnt+=1
                if cnt>max_texts:
                    break
    cid_to_texts[cid]=texts

  0%|          | 0/9503 [00:00<?, ?it/s]

100%|██████████| 9503/9503 [02:49<00:00, 55.91it/s]  


In [5]:
import sys
import numpy as np
sys.path.append("../01web_codes")
from gensim.models.fasttext import load_facebook_model
from tqdm import tqdm
from src.classify.Text2Vec import Text2Vec

t2v = Text2Vec(load_facebook_model('../data/model/cc.ja.300.bin'))

In [6]:
#各カテゴリのテキストをベクトル化
cid_to_vecs={}
check_length=100
for cid, texts in tqdm(cid_to_texts.items()):
    vecs = [t2v.text2vec(i[:check_length]) for i in texts]
    vecs=np.array(vecs)
    vecs=np.mean(vecs, axis=0)
    cid_to_vecs[cid]=vecs



 99%|█████████▉| 9430/9503 [22:39<00:00, 798.55it/s] /home/hatakeyama/miniconda3/envs/textprocess/lib/python3.12/site-packages/numpy/core/fromnumeric.py:3504: RuntimeWarning: Mean of empty slice.
  return _methods._mean(a, axis=axis, dtype=dtype,
/home/hatakeyama/miniconda3/envs/textprocess/lib/python3.12/site-packages/numpy/core/_methods.py:129: RuntimeWarning: invalid value encountered in scalar divide
  ret = ret.dtype.type(ret / rcount)
100%|██████████| 9503/9503 [22:39<00:00,  6.99it/s] 


In [20]:
vec_array=list(cid_to_vecs.values())
vec_array=[i for i in vec_array if i.shape==(300,)]
vecs.shape

(300,)

In [21]:
n_clusters=5
from sklearn.cluster import MiniBatchKMeans,KMeans
vec_array=np.array(vec_array)
# k-meansクラスタリング
print("clustering...")
kmeans = KMeans(n_clusters=n_clusters, random_state=1).fit(vec_array)

clustering...


In [24]:
cid_to_label={}
for cid, vec in cid_to_vecs.items():
    try:
        label=kmeans.predict([vec])[0]
        cid_to_label[cid]=label
    except Exception as e:
        print(cid,e)

7936 Expected 2D array, got 1D array instead:
array=[nan].
Reshape your data either using array.reshape(-1, 1) if your data has a single feature or array.reshape(1, -1) if it contains a single sample.


In [25]:
label_to_path_list={}
for cid, label in cid_to_label.items():
    if str(label) not in label_to_path_list:
        label_to_path_list[str(label)]=[]
    path=f"../data/dedup_categorized/{cid}/*.jsonl"
    label_to_path_list[str(label)].append(path)


In [26]:
import json
with open("../data/clustered_path.json", "w") as f:
    json.dump(label_to_path_list, f, indent=4)

In [27]:
#行数をwcで数える
import os
import subprocess
label_to_article_count={}
for label, s_path_list in label_to_path_list.items():
    label_to_article_count[label]=0
    for s_path in s_path_list:
        for path in glob.glob(s_path):
            res=os.system(f"wc -l {path}")
            result = subprocess.run(["wc", "-l"] + path.split(), capture_output=True, text=True)
            # 出力から合計行数を抽出
            count=result.stdout.split(" ")[0]
            label_to_article_count[label] += int(count)

12 ../data/dedup_categorized/5538/c4-ja.tfrecord-00689-of-01024.jsonl
10 ../data/dedup_categorized/5538/c4-ja.tfrecord-00694-of-01024.jsonl
9 ../data/dedup_categorized/5538/c4-ja.tfrecord-00103-of-01024.jsonl
7 ../data/dedup_categorized/5538/c4-ja.tfrecord-00752-of-01024.jsonl
9 ../data/dedup_categorized/5538/c4-ja.tfrecord-00363-of-01024.jsonl
6 ../data/dedup_categorized/5538/c4-ja.tfrecord-00026-of-01024.jsonl
10 ../data/dedup_categorized/5538/c4-ja.tfrecord-00316-of-01024.jsonl
1 ../data/dedup_categorized/5538/cc2021_batch1-1_0l.jsonl
7 ../data/dedup_categorized/5538/cc2021_batch25-5_0l.jsonl
8 ../data/dedup_categorized/5538/cc2021_batch37-2_0l.jsonl
18 ../data/dedup_categorized/5538/cc100_ja_167l.jsonl
3 ../data/dedup_categorized/5538/oscar_ja_102l.jsonl
4 ../data/dedup_categorized/5538/c4-ja.tfrecord-00466-of-01024.jsonl
7 ../data/dedup_categorized/5538/c4-ja.tfrecord-00649-of-01024.jsonl
6 ../data/dedup_categorized/5538/c4-ja.tfrecord-00327-of-01024.jsonl
5 ../data/dedup_categori

In [ ]:

with open("../data/clustered_n.json", "w") as f:
    json.dump(label_to_article_count, f, indent=4)

In [ ]:
for i in range(n_clusters):
    print("--------\ncluster: ",i)
    cc1_loader=CommonCrawlDataset(label_to_path_list[str(i)])
    cc1_iter=iter(cc1_loader)
    for i in range(5):
        print(next(cc1_iter))

{'text': '地方創生スタートから2年成否を分けるカギはどこに?\n地方創生の検証と対策\n「地方創生」が政策として掲げられて早2年。各地の状況をつぶさに観察すると、停滞ないしは衰退し続けるところと、上向くところの「差異」が徐々に顕在化してきている。それは何に起因するのか?創生の成否を分けるカギについて、具体的に検討してみたい。\n創生成功のカギ「長期的視点」\n現政権が推進する「地方創生」は、国として大きな枠組みを用意し、必要に応じてサポートを行うものの、基本的には、各地域が、自らの叡智によって、その地でサバイブすることを求める点に特徴がある。\nここで言う「叡智」は2つある。\n1つ目は、「長期的視点」である。「国家100年の計」というが、地域の創生も本来それに準じるものだ。50年後、100年後にどんな地域になっていたいのかが“明確"で、地域内外の人々が、「自分もその一助となりたい」と思えるほど“魅力的"な、そして“環境変化の風雪に耐え得る力のある"理念・哲学をもった長期的プランニングが望まれる。\nザルツブルク音楽祭を核に、音楽・文化の街として世界中から観光客が訪れるオーストリアのザルツブルク。約100年前は、何の特徴もない寂れ果てた街だったPhoto by Wikimedia\n一例を挙げよう。オーストリアのザルツブルクは、“名実ともに世界一"と評される祝祭(＝ザルツブルク音楽祭)を核に、多数の自然・歴史遺産を擁する人気観光リゾートである。しかし、100年近く前、同市は、人口3万の過疎の町であった。第一次大戦に破れた祖国オーストリア(ハプスブルク帝国)は、欧州の周縁部の1小国になり下がり、ザルツブルクも、“モーツァルト生誕地"という以外、何の特徴もない寂れ果てた街だったのである。\nところが、ここに、「演劇界の皇帝」マックス・ラインハルト、文豪フーゴー・フォン・ホーフマンスタール、大作曲家リヒャルト・シュトラウスが集い、“モーツァルトの音楽と演劇理念の復権・再生"を目指し、1920年夏、「ザルブルク・フェスティバル」(ザルツブルク音楽祭)を創始する。\nそして、その理念の延長上に、やがて、冬の「モーツァルト週間」(1956～)、春の「復活祭音楽祭」(「指揮界の帝王」ヘルベルト・フォン・カラヤンが創始、1967～)などの音楽祭群を加えてゆく。さらには、ミ

In [ ]:
#モデル保存
import pickle
with open("../data/second_kmeans_model.pkl", "wb") as f:
    pickle.dump(kmeans, f)